In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os
import sys
from pathlib import Path

# check if workding_dir is in local variables
if "workding_dir" not in locals():
    workding_dir = str(Path.cwd().parent)

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /Users/inflaton/code/engd/papers/rapget-translation


In [3]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /Users/inflaton/code/engd/papers/rapget-translation/.env


True

In [4]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("DATA_PATH")
results_path = os.getenv("RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"
max_new_tokens = int(os.getenv("MAX_NEW_TOKENS", 2048))

print(
    model_name,
    adapter_name_or_path,
    load_in_4bit,
    data_path,
    results_path,
    use_english_datasets,
    max_new_tokens,
)

Qwen/Qwen2-7B-Instruct None False datasets/mac/mac.tsv results/mac-results.csv False 300


In [5]:
%%time
os.environ["TOKENIZERS_PARALLELISM"] = "true"

!python --version
!pip show torch transformers

Python 3.11.9
Name: torch
Version: 2.4.0
Summary: Tensors and Dynamic neural networks in Python with strong GPU acceleration
Home-page: https://pytorch.org/
Author: PyTorch Team
Author-email: packages@pytorch.org
License: BSD-3
Location: /Users/inflaton/anaconda3/envs/rapget/lib/python3.11/site-packages
Requires: filelock, fsspec, jinja2, networkx, sympy, typing-extensions
Required-by: accelerate, peft, torchaudio, torchvision
---
Name: transformers
Version: 4.43.3
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: /Users/inflaton/anaconda3/envs/rapget/lib/python3.11/site-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tokenize

In [6]:
from llm_toolkit.llm_utils import *
from llm_toolkit.translation_utils import *

device = check_gpu()

[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/inflaton/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to /Users/inflaton/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     /Users/inflaton/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


loading: /Users/inflaton/code/engd/papers/rapget-translation/eval_modules/calc_repetitions.py
loading /Users/inflaton/code/engd/papers/rapget-translation/llm_toolkit/translation_utils.py


[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/inflaton/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to /Users/inflaton/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     /Users/inflaton/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


MPS is available


In [7]:
model, tokenizer = load_model(model_name)

loading model: Qwen/Qwen2-7B-Instruct with adapter: None


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

In [8]:
dataset = load_translation_dataset(data_path, tokenizer=tokenizer, num_shots=5)

loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 1133
    })
})


In [9]:
dataset["test"]["chinese"][260], dataset["test"]["chinese"][908]

('那刘姥姥先听见告艰苦，只当是没想头了， 又听见给他二十两银子，喜的眉开眼笑道：“我们也知道艰难的，但只俗语说的：‘瘦死的骆驼比马还大’呢。',
 '后来她不挣扎了，对我说，混蛋，你要把我怎么办。')

In [10]:
eval_dataset = dataset["test"].select([260, 908])

In [11]:
print_row_details(eval_dataset.to_pandas(), range(len(eval_dataset)))

--------------------------------------------------
chinese: 那刘姥姥先听见告艰苦，只当是没想头了， 又听见给他二十两银子，喜的眉开眼笑道：“我们也知道艰难的，但只俗语说的：‘瘦死的骆驼比马还大’呢。
--------------------------------------------------
english: When Grannie Liu heard Xi-feng talk about 'difficulties' she concluded that there was no hope. Her delight and the way in which her face lit up with pleasure when she heard that she was, after all, to be given twenty taels of silver can be imagined. 'We knew you had your troubles,' she said, 'but as the saying goes, 'A starved camel is bigger than a fat horse.'
--------------------------------------------------
text: <|im_start|>system
You are a helpful assistant that translates Chinese to English.<|im_end|>
<|im_start|>user
You will be given a Chinese sentence to translate. If it is an incomplete sentence, or if you are unsure about the meaning, simply copy the input text as your output. Do not output any additional sentence such as explanation or reasoning.

Example Translations:
Chinese: 全仗着狐仙搭救。

In [12]:
predictions = eval_model(
    model, tokenizer, eval_dataset, device=device, max_new_tokens=max_new_tokens
)

 50%|█████     | 1/2 [01:54<01:54, 114.95s/it]

Batch output: ['When she first heard that they were in dire straits, she thought that all hope was lost. But when she heard that they were to receive twenty taels of silver, she beamed with delight and said, "We understand their difficulties, but as the saying goes, \'a skinny camel is bigger than a horse\'."']


100%|██████████| 2/2 [02:34<00:00, 77.40s/it] 


In [13]:
print(predictions)

['When she first heard that they were in dire straits, she thought that all hope was lost. But when she heard that they were to receive twenty taels of silver, she beamed with delight and said, "We understand their difficulties, but as the saying goes, \'a skinny camel is bigger than a horse\'."', 'Later, she stopped struggling and said to me, "You bastard, what are you going to do to me?"']


In [17]:
from llm_toolkit.translation_utils_v1 import (
    load_translation_dataset as load_translation_dataset_v1,
)

dataset_v1 = load_translation_dataset_v1(data_path, tokenizer=tokenizer)

loading train/test data files


Map:   0%|          | 0/4528 [00:00<?, ? examples/s]

Map:   0%|          | 0/1133 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 1133
    })
})


In [18]:
print_row_details(dataset_v1["test"].to_pandas())

--------------------------------------------------
chinese: 老耿端起枪，眯缝起一只三角眼，一搂扳机响了枪，冰雹般的金麻雀劈哩啪啦往下落，铁砂子在柳枝间飞迸着，嚓嚓有声。
--------------------------------------------------
english: Old Geng picked up his shotgun, squinted, and pulled the trigger. Two sparrows crashed to the ground like hailstones as shotgun pellets tore noisily through the branches.
--------------------------------------------------
text: <|im_start|>system
You are an expert in translating Chinese to English.<|im_end|>
<|im_start|>user
Please translate the following Chinese text into English and provide only the translated content, nothing else.
老耿端起枪，眯缝起一只三角眼，一搂扳机响了枪，冰雹般的金麻雀劈哩啪啦往下落，铁砂子在柳枝间飞迸着，嚓嚓有声。<|im_end|>
<|im_start|>assistant
Old Geng picked up his shotgun, squinted, and pulled the trigger. Two sparrows crashed to the ground like hailstones as shotgun pellets tore noisily through the branches.<|im_end|>
--------------------------------------------------
prompt: <|im_start|>system
You are an expert in translating Chinese

In [19]:
eval_dataset_v1 = dataset_v1["test"].select([260, 908])
predictions_v1 = eval_model(
    model, tokenizer, eval_dataset_v1, device=device, max_new_tokens=max_new_tokens
)
predictions_v1

 50%|█████     | 1/2 [01:14<01:14, 74.72s/it]

Batch output: ['At first, when Old Lady Liu heard that there was no hope, she thought that was the end of it. But when she heard that twenty taels of silver would be given to her, she beamed with delight, saying with a smile, "We understand the hardships, but as the old saying goes, \'a skinny camel is bigger than a horse.\' "']


100%|██████████| 2/2 [01:46<00:00, 53.02s/it]


['At first, when Old Lady Liu heard that there was no hope, she thought that was the end of it. But when she heard that twenty taels of silver would be given to her, she beamed with delight, saying with a smile, "We understand the hardships, but as the old saying goes, \'a skinny camel is bigger than a horse.\' "',
 'Later, she stopped struggling and said to me, "F*ck, what are you going to do with me?"']

In [20]:
dataset_v2 = load_translation_dataset(data_path, tokenizer=tokenizer, num_shots=0)

loading train/test data files


Map:   0%|          | 0/4528 [00:00<?, ? examples/s]

Map:   0%|          | 0/1133 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 1133
    })
})


In [21]:
eval_dataset_v2 = dataset_v2["test"].select([260, 908])
predictions_v2 = eval_model(
    model, tokenizer, eval_dataset_v2, device=device, max_new_tokens=max_new_tokens
)
predictions_v2

 50%|█████     | 1/2 [01:02<01:02, 62.37s/it]

Batch output: ['That Lady Liu, having first heard that there was no hope, thought that things must be bad. But when she heard that she would receive twenty taels of silver, she smiled and said, "We know how hard it is, but the saying goes: \'A skinny camel is bigger than a horse.\'"']


100%|██████████| 2/2 [01:20<00:00, 40.10s/it]


['That Lady Liu, having first heard that there was no hope, thought that things must be bad. But when she heard that she would receive twenty taels of silver, she smiled and said, "We know how hard it is, but the saying goes: \'A skinny camel is bigger than a horse.\'"',
 'Later, she stopped struggling and said to me, "F*ck, what are you going to do with me?"']